![tracker](https://us-central1-vertex-ai-mlops-369716.cloudfunctions.net/pixel-tracking?path=statmike%2Fvertex-ai-mlops%2FApplied+GenAI%2Flegacy&file=Summarize+Conversations+-+Text+and+Audio.ipynb)
<!--- header table --->
<table align="left">
  <td style="text-align: center">
    <a href="https://colab.research.google.com/github/statmike/vertex-ai-mlops/blob/main/Applied%20GenAI/legacy/Summarize%20Conversations%20-%20Text%20and%20Audio.ipynb">
      <img src="https://cloud.google.com/ml-engine/images/colab-logo-32px.png" alt="Google Colaboratory logo">
      <br>Run in<br>Colab
    </a>
  </td>
  <td style="text-align: center">
    <a href="https://console.cloud.google.com/vertex-ai/colab/import/https%3A%2F%2Fraw.githubusercontent.com%2Fstatmike%2Fvertex-ai-mlops%2Fmain%2FApplied%2520GenAI%2Flegacy%2FSummarize%2520Conversations%2520-%2520Text%2520and%2520Audio.ipynb">
      <img width="32px" src="https://lh3.googleusercontent.com/JmcxdQi-qOpctIvWKgPtrzZdJJK-J3sWE1RsfjZNwshCFgE_9fULcNpuXYTilIR2hjwN" alt="Google Cloud Colab Enterprise logo">
      <br>Run in<br>Colab Enterprise
    </a>
  </td>      
  <td style="text-align: center">
    <a href="https://github.com/statmike/vertex-ai-mlops/blob/main/Applied%20GenAI/legacy/Summarize%20Conversations%20-%20Text%20and%20Audio.ipynb">
      <img src="https://cloud.google.com/ml-engine/images/github-logo-32px.png" alt="GitHub logo">
      <br>View on<br>GitHub
    </a>
  </td>
  <td style="text-align: center">
    <a href="https://console.cloud.google.com/vertex-ai/workbench/deploy-notebook?download_url=https://raw.githubusercontent.com/statmike/vertex-ai-mlops/main/Applied%20GenAI/legacy/Summarize%20Conversations%20-%20Text%20and%20Audio.ipynb">
      <img src="https://lh3.googleusercontent.com/UiNooY4LUgW_oTvpsNhPpQzsstV5W8F7rYgxgGBD85cWJoLmrOzhVs_ksK_vgx40SHs7jCqkTkCk=e14-rj-sc0xffffff-h130-w32" alt="Vertex AI logo">
      <br>Open in<br>Vertex AI Workbench
    </a>
  </td>
</table>

---

**File Move Notices**

This file moved locations:
- On 09/07/2024 (mm/dd/yyyy)
	- From: `Applied GenAI/Summarize Conversations - Text and Audio.ipynb`
	- To: `Applied GenAI/legacy/Summarize Conversations - Text and Audio.ipynb`
---
<!---end of move notices--->

## Summarize Conversations Using Large Language Models - For Text and Audio Conversations

The Flow:
- Setup the environment: installs, APIs, parameters, packages, and clients
- Create some baseline data - text transcript of call to customer service
- Use Vertex LLMs
    - Continue a chat using an LLM as the Customer Service Agent
    - Summarize a chat using an LLM
- Audio Processing
    - Turn a chat transcript into an audio file for use in this example. Use different voices for the customer and the agent.
    - Transcribe the audio with speaker diarization (differentiate who is speaking).
- Use LLM to Create a summary of the chat transcript



---
## Colab Setup

To run this notebook in Colab click [![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/statmike/vertex-ai-mlops/blob/main/Applied%20GenAI/Summarize%20Conversations%20-%20Text%20and%20Audio.ipynb) and run the cells in this section.  Otherwise, skip this section.

This cell will authenticate to GCP (follow prompts in the popup).

In [1]:
PROJECT_ID = 'statmike-mlops-349915' # replace with project ID

In [2]:
try:
    import google.colab
    from google.colab import auth
    auth.authenticate_user()
    !gcloud config set project {PROJECT_ID}
    # Text-To-Speech and Speech-To-Text Run as a service account - authorize default:
    !gcloud auth application-default login --quiet
except Exception:
    pass

---
## Installs

The list `packages` contains tuples of package import names and install names.  If the import name is not found then the install name is used to install quitely for the current user.

In [3]:
# tuples of (import name, install name, min_version)
packages = [
    ('google.cloud.aiplatform', 'google-cloud-aiplatform'),
    ('google.cloud.speech', 'google-cloud-speech'),
    ('google.cloud.texttospeech', 'google-cloud-texttospeech'),
    ('google.cloud.dlp', 'google-cloud-dlp')
]

import importlib
install = False
for package in packages:
    if not importlib.util.find_spec(package[0]):
        print(f'installing package {package[1]}')
        install = True
        !pip install {package[1]} -U -q --user
    elif len(package) == 3:
        if importlib.metadata.version(package[0]) < package[2]:
            print(f'updating package {package[1]}')
            install = True
            !pip install {package[1]} -U -q --user

### API Enablement

In [4]:
!gcloud services enable speech.googleapis.com
!gcloud services enable texttospeech.googleapis.com
!gcloud services enable aiplatform.googleapis.com
!gcloud services enable dlp.googleapis.com

### Restart Kernel (If Installs Occured)

After a kernel restart the code submission can start with the next cell after this one.

In [5]:
if install:
    import IPython
    app = IPython.Application.instance()
    app.kernel.do_shutdown(True)

---
## Setup

In [6]:
project = !gcloud config get-value project
PROJECT_ID = project[0]
PROJECT_ID

'statmike-mlops-349915'

In [7]:
REGION = 'us-central1'
SERIES = 'applied-genai'
EXPERIMENT = 'summarize-audio-conversation'

# change the following if the GCS bucket has a different name than the PROJECT_ID
GCS_BUCKET = PROJECT_ID

In [8]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'

import IPython.display
import wave
import io
import json

import vertexai.language_models
from vertexai.language_models import InputOutputTextPair
from google.cloud import texttospeech as tts
from google.cloud import speech as stt
from google.cloud import dlp_v2 as dlp

In [9]:
vertexai.init(project = PROJECT_ID, location = REGION)
tts_client = tts.TextToSpeechClient()
stt_client = stt.SpeechClient()
dlp_client = dlp.DlpServiceClient()

---
## Baseline Data For Example

Create a chat dialogue as text!  For this example I am using the data `InputOutputTextPair` for the Vertex AI SDK - [link](https://cloud.google.com/python/docs/reference/aiplatform/latest/vertexai.language_models.InputOutputTextPair).  Create the conversation as a list of interactions:

```JSON
conversation = [
    InputOutputTextPair(
        input_text = '',
        output_text = ''
    ),
    ...,
    InputOutputTextPair(
        input_text = '',
        output_text = ''
    )
]
```

In [10]:
conversation = [
    InputOutputTextPair(
        input_text = "Hello",
        output_text = "Thank you for calling Google Cloud Support. How may I assist you today Mr. Henderson?"
    ),
    InputOutputTextPair(
        input_text = "Hi, I am trying to create a Google Cloud account and use the free credits, but I am not sure where to start.",
        output_text = "Sure, I can definitely help you with that. May I know if you already have a Google account?"
    ),
    InputOutputTextPair(
        input_text = "Yes, I do. My account number is 1 2 3 4 5 6 7 8 9",
        output_text = "Great. The first step would be to sign in to the Google Cloud Console. Do you know how to access it?"
    ),
    InputOutputTextPair(
        input_text = "No, I don't. Can you guide me?",
        output_text = "Sure. Please go to console.cloud.google.com and sign in with your Google account credentials. Once you are signed in, you will be directed to the Google Cloud Console dashboard."
    ),
    InputOutputTextPair(
        input_text = "Okay, I have signed in. What should I do next?",
        output_text = "Now, you'll need to create a project. A project is a collection of resources, such as Compute Engine instances and Cloud Storage buckets. To create a project, click on the 'Projects' tab and then click on the 'Create project' button. You'll need to provide a name for your project and then select a region. Once you've created your project, you'll be able to start using the free credits."
    ),
    InputOutputTextPair(
        input_text = "Great, I've created my project. Now what?",
        output_text = "Now, you'll need to enable the free trial. To do this, click on the 'Billing' tab and then click on the 'Enable free trial' button. You'll need to provide your credit card information and then click on the 'Submit' button."
    ),
    InputOutputTextPair(
        input_text = "Alright, I think I can do that.",
        output_text = "Excellent. You've now successfully created a Google Cloud account. You can start using the free credits that are available by clicking on the 'Credits' tab."
    ),
    InputOutputTextPair(
        input_text = "That sounds easy enough. How much free credit do I get?",
        output_text = "You'll receive $300 worth of free credit that you can use on any Google Cloud services for up to 12 months."
    ),
    InputOutputTextPair(
        input_text = "Is there anything else I should know?",
        output_text = "Yes, just be sure to keep an eye on your usage during your free trial period. Once your credits are used up, you'll start being charged for any additional usage. But don't worry, you'll receive notifications when you're approaching your credit limit."
    ),
    InputOutputTextPair(
        input_text = "Thank you so much for your help!",
        output_text = "You're welcome. Is there anything else I can help you with today?"
    ),
    InputOutputTextPair(
        input_text = "No, that's all. Thank you again!",
        output_text = "You're welcome. Have a great day and enjoy using Google Cloud!"
    ),
]

---
## Using Vertex AI LLM's

### LLM Chat Agent

In [12]:
chat_model = vertexai.language_models.ChatModel.from_pretrained('chat-bison')

Let's truncate the full conversation in `conversation` from above, and use it to start chatting with LLM Chat Agent!

In [13]:
conversation_so_far = conversation[0:-3]

In [14]:
chat = chat_model.start_chat(
    context = 'I am a customer service agent.',
    examples = conversation_so_far
)

Now, continue the conversation with the same inputs as before but let the Chat Agent reply:

In [15]:
print(conversation[-3].input_text)
response = chat.send_message(conversation[-3].input_text)
response.text

Is there anything else I should know?


" Yes, there are a few things you should keep in mind. First, the free credits will expire after 12 months, so be sure to use them before then. Second, the free credits can only be used on Google Cloud services, so you can't use them to purchase other products or services. Finally, the free credits are subject to Google's terms and conditions, so be sure to read them carefully before you start using them."

Continue!

In [16]:
print(conversation[-2].input_text)
response = chat.send_message(conversation[-2].input_text)
response.text

Thank you so much for your help!


" You're welcome! I'm glad I could help. If you have any other questions, please don't hesitate to ask."

In [17]:
print(conversation[-1].input_text)
response = chat.send_message(conversation[-1].input_text)
response.text

No, that's all. Thank you again!


" You're welcome! Have a great day!"

### LLM To Summarize The Conversation

In [18]:
chat.message_history

[ChatMessage(content='Is there anything else I should know?', author='user'),
 ChatMessage(content=" Yes, there are a few things you should keep in mind. First, the free credits will expire after 12 months, so be sure to use them before then. Second, the free credits can only be used on Google Cloud services, so you can't use them to purchase other products or services. Finally, the free credits are subject to Google's terms and conditions, so be sure to read them carefully before you start using them.", author='bot'),
 ChatMessage(content='Thank you so much for your help!', author='user'),
 ChatMessage(content=" You're welcome! I'm glad I could help. If you have any other questions, please don't hesitate to ask.", author='bot'),
 ChatMessage(content="No, that's all. Thank you again!", author='user'),
 ChatMessage(content=" You're welcome! Have a great day!", author='bot')]

Combine the conversation history in `conversation_so_far` with the agent assisted continuation in `chat.message_history`:

In [19]:
chat_history = ''.join(
    [f"\nspeaker 1: {c.input_text}\nspeaker 2: {c.output_text}" for c in conversation_so_far] +
    [f"\nspeaker {1 + int(m.author == 'bot')}: {m.content}" for m in chat.message_history]
)
print(chat_history)


speaker 1: Hello
speaker 2: Thank you for calling Google Cloud Support. How may I assist you today Mr. Henderson?
speaker 1: Hi, I am trying to create a Google Cloud account and use the free credits, but I am not sure where to start.
speaker 2: Sure, I can definitely help you with that. May I know if you already have a Google account?
speaker 1: Yes, I do. My account number is 1 2 3 4 5 6 7 8 9
speaker 2: Great. The first step would be to sign in to the Google Cloud Console. Do you know how to access it?
speaker 1: No, I don't. Can you guide me?
speaker 2: Sure. Please go to console.cloud.google.com and sign in with your Google account credentials. Once you are signed in, you will be directed to the Google Cloud Console dashboard.
speaker 1: Okay, I have signed in. What should I do next?
speaker 2: Now, you'll need to create a project. A project is a collection of resources, such as Compute Engine instances and Cloud Storage buckets. To create a project, click on the 'Projects' tab an

Generate a summary with an LLM:

In [21]:
text_model = vertexai.language_models.TextGenerationModel.from_pretrained('text-bison')

In [22]:
summary = text_model.predict(f"Summarize the following conversation\n{chat_history}")

In [23]:
summary.safety_attributes

{'Derogatory': 0.1, 'Finance': 1.0, 'Insult': 0.1}

In [24]:
print(summary.text)

 A customer named Mr. Henderson contacted Google Cloud Support to set up a Google Cloud account and utilize the free credits offered. The support representative guided him through the process, starting with signing in to the Google Cloud Console using his existing Google account. The representative explained how to create a project and enable the free trial by providing credit card information. The customer was informed that they would receive $300 worth of free credit valid for 12 months and could be used on any Google Cloud services. The representative also mentioned important details such as the expiration of free credits, usage restrictions to Google Cloud services, and adherence to Google's terms and


In [26]:
text_model.predict(f"Summarize the following conversation from each persons point of view\n{chat_history}")

 **Speaker 1 (Mr. Henderson):**
- Needed assistance in creating a Google Cloud account and utilizing the free credits.
- Provided his Google account number.
- Followed the instructions to sign in to the Google Cloud Console, create a project, and enable the free trial.
- Expressed understanding of the free credit usage and its limitations.
- Appreciated the detailed guidance and thanked the support representative.

**Speaker 2 (Google Cloud Support):**
- Offered assistance in creating a Google Cloud account and using free credits.
- Guided Mr. Henderson through the process of signing in to the Google Cloud Console

---
## Audio

How do we recreate the summary process above when the source is Audio?  Speech-To-Text then Text-To-Speech.

Use multiple voices and then detect the different voices as speakers in the audio.

### First, Create Audio

We don't have audio but we do have the actual transcript.  Here, the [Cloud Text-To-Speech API](https://cloud.google.com/text-to-speech/docs/before-you-begin) is used to create an audio conversation.

In [27]:
voice_1 = tts.VoiceSelectionParams(language_code = "en-US", name = 'en-US-Studio-M')
voice_2 = tts.VoiceSelectionParams(language_code = "en-US", name = 'en-US-Studio-O')
audio = tts.AudioConfig(audio_encoding = tts.AudioEncoding.LINEAR16, speaking_rate = 1, sample_rate_hertz = 16000)

Create wave files for each speakers turn in the conversation:

In [28]:
waves = []
for c in conversation:
    input_1 = tts.SynthesisInput(text = c.input_text)
    response_1 = tts_client.synthesize_speech(input = input_1, voice = voice_1, audio_config = audio)
    input_2 = tts.SynthesisInput(text = c.output_text)
    response_2 = tts_client.synthesize_speech(input = input_2, voice = voice_2, audio_config = audio)
    waves += [response_1.audio_content, response_2.audio_content]

In [29]:
len(waves), type(waves[0])

(22, bytes)

Open all the wave files and get parameters and data:

In [30]:
wave_data = []
for w in waves:
    w_data = wave.open(io.BytesIO(w))
    wave_data.append([w_data.getparams(), w_data.readframes(w_data.getnframes())])
    w_data.close()

Concatenate all the wave data into a single `.wav` file:

In [31]:
output = wave.open('audio_conversation.wav', 'wb')
output.setparams(wave_data[0][0])
for i in range(len(wave_data)):
    output.writeframes(wave_data[i][1])
output.close()

In [32]:
IPython.display.Audio("audio_conversation.wav")

Move the file to GCS:

In [33]:
!gsutil mv audio_conversation.wav gs://{GCS_BUCKET}/{SERIES}/{EXPERIMENT}/

Copying file://audio_conversation.wav [Content-Type=audio/x-wav]...
Removing file://audio_conversation.wav...                                       

Operation completed over 1 objects/3.7 MiB.                                      


### Now, Turn Audio To Text

And recognize the different speakers!

[google.cloud.speech_v1.types.RecognitionConfig](https://cloud.google.com/python/docs/reference/speech/latest/google.cloud.speech_v1.types.RecognitionConfig)

In [34]:
audio = stt.RecognitionAudio(uri = f'gs://{GCS_BUCKET}/{SERIES}/{EXPERIMENT}/audio_conversation.wav')

In [35]:
diarization_config = stt.SpeakerDiarizationConfig(
    enable_speaker_diarization = True,
    min_speaker_count = 2,
    max_speaker_count = 2,
)

In [36]:
config = stt.RecognitionConfig(
    encoding = stt.RecognitionConfig.AudioEncoding.LINEAR16,
    sample_rate_hertz = 16000,
    language_code = "en-US",
    model = "latest_long",
    audio_channel_count = 1,
    enable_automatic_punctuation = True,
    enable_word_time_offsets = True,
    diarization_config = diarization_config
)

In [37]:
operation = stt_client.long_running_recognize(config = config, audio = audio)

In [38]:
response = operation.result(timeout = 90)

In [39]:
type(response)

google.cloud.speech_v1.types.cloud_speech.LongRunningRecognizeResponse

Check out the structure of this response:
    
[google.cloud.speech_v1.types.LongRunningRecognizeResponse](https://cloud.google.com/python/docs/reference/speech/latest/google.cloud.speech_v1.types.LongRunningRecognizeResponse)

In [40]:
len(response.results), type(response.results[-1])

(3, google.cloud.speech_v1.types.cloud_speech.SpeechRecognitionResult)

It's a list of this structure:

[google.cloud.speech_v1.types.SpeechRecognitionResult](https://cloud.google.com/python/docs/reference/speech/latest/google.cloud.speech_v1.types.SpeechRecognitionResult)

In [41]:
len(response.results[-1].alternatives), type(response.results[-1].alternatives[-1])

(1, google.cloud.speech_v1.types.cloud_speech.SpeechRecognitionAlternative)

And these `alternatives` are of this structure:

[google.cloud.speech_v1.types.SpeechRecognitionAlternative](https://cloud.google.com/python/docs/reference/speech/latest/google.cloud.speech_v1.types.SpeechRecognitionAlternative)

Note, with diarization the last of these `alternatives` (index = -1) is the actual word by word diarization with speaker tags.

In [42]:
response.results[-1].alternatives[0].words[0]

start_time {
}
end_time {
  nanos: 200000000
}
word: "Hello."
speaker_tag: 1
speaker_label: "1"

Make a chat transcript with the speakers marked:

In [43]:
chat_transcript = ''
speaker = 0
speaker_transcript = ''
for word in response.results[-1].alternatives[0].words:
    if word.speaker_tag != speaker:
        if speaker > 0: chat_transcript += f"\nspeaker {speaker}: {speaker_transcript}"
        speaker = word.speaker_tag
        speaker_transcript = word.word
    else:
        speaker_transcript += f" {word.word}"

In [44]:
print(chat_transcript)


speaker 1: Hello.
speaker 2: Thank you for calling Google Cloud support. How may I assist you? Today, Mr. Henderson.
speaker 1: Hi, I am trying to create a Google Cloud account and use the free credits but I am not sure where to start
speaker 2: sure. I can definitely help you with that. May I know if you already have a Google account?
speaker 1: Yes, I do. My account number is one two, three, four, five six, seven eight nine
speaker 2: great. The first step would be to sign into the Google Cloud console. Do you know how to access it?
speaker 1: No, I don't. Can you guide me?
speaker 2: Sure, please go to console.cloud.google.com and sign in with your Google account credentials. Once you are signed in you will be directed to the Google Cloud console dashboard.
speaker 1: Okay, I have signed in what should I do next
speaker 2: now, you'll need to create a project a project is a collection of resources such as compute engine instances and cloud storage buckets to create a project click 

## Remove Sensitive Information From The Transcript

Use Cloud DLP To remove account numbers and Name.

[Python API Guide](https://cloud.google.com/python/docs/reference/dlp/latest)
[Documentation Link](https://cloud.google.com/dlp/docs/deidentify-sensitive-data)
[Info Types](https://cloud.google.com/dlp/docs/infotypes-reference)

In [45]:
info_types = ["GENDER", "AGE", "URL", "FIRST_NAME", "LAST_NAME", "LOCATION", "TIME", "STREET_ADDRESS", "GENERIC_ID"]

inspect_config = dict(
    info_types = [dict(name = i) for i in info_types]
)
deidentify_config = dict(
    info_type_transformations = dict(
        transformations = [dict(primitive_transformation = dict(replace_config = dict(new_value = dict(string_value = 'HEYEHEYEYHHE'))))]    
    )
)
deidentify_config = dict(
    info_type_transformations = dict(
        transformations = [dict(primitive_transformation = dict(replace_with_info_type_config = dict()))]    
    )
)

In [46]:
response = dlp_client.deidentify_content(
    request = dict(
        parent = f"projects/{PROJECT_ID}",
        deidentify_config = deidentify_config,
        inspect_config = inspect_config,
        item = dict(value = chat_transcript)
    )
)

In [47]:
print(response.item.value)


speaker 1: Hello.
speaker 2: Thank you for calling Google Cloud support. How may I assist you? Today, Mr. [LAST_NAME].
speaker 1: Hi, I am trying to create a Google Cloud account and use the free credits but I am not sure where to start
speaker 2: sure. I can definitely help you with that. May I know if you already have a Google account?
speaker 1: Yes, I do. My account number is one two, three, four, five six, seven eight nine
speaker 2: great. The first step would be to sign into the Google Cloud console. Do you know how to access it?
speaker 1: No, I don't. Can you guide me?
speaker 2: Sure, please go to [URL] and sign in with your Google account credentials. Once you are signed in you will be directed to the Google Cloud console dashboard.
speaker 1: Okay, I have signed in what should I do next
speaker 2: now, you'll need to create a project a project is a collection of resources such as compute engine instances and cloud storage buckets to create a project click on the projects T

In [48]:
redacted_chat_transcript = response.item.value

## Summarize The Audio Transcript

As shown above, the transcript can be summarize with the an LLM as follows: 

In [49]:
text_model.predict(f"Summarize the following conversation: \n{redacted_chat_transcript}")

 A customer contacts Google Cloud support to set up an account and use the free credits. The support representative guides the customer through the process, including signing into the Google Cloud console, creating a project, enabling the free trial, and understanding the free credit usage. The customer is informed that they will receive $300 worth of free credit for 12 months and should monitor their usage to avoid additional charges. The customer expresses gratitude for the assistance, and the conversation ends with the support representative checking if there are any other concerns.

You can even get a summary from each speakers point of view:

In [50]:
text_model.predict(f"Summarize the following conversation from the point of view of each speaker. Speaker 1 is new to Google Cloud and not certain how to get started. List 1 thing that could be done better to help each speaker.:\n{redacted_chat_transcript}")

 **Speaker 1**: 
- I needed help getting started with Google Cloud and creating an account.
- The support agent guided me through the process of signing in, creating a project, and enabling the free trial.
- I received information about the free credits and how to monitor my usage.

**One thing that could be done better**: 
- Provide a more detailed explanation of the Google Cloud console and its features.

**Speaker 2**: 
- Assisted a new Google Cloud user in creating an account and using the free credits.
- Provided step-by-step instructions on how to sign in,

## Label The Transcripts Speaker By Role

In [52]:
speaker_map = text_model.predict(f"""
Create a JSON structure from the transcript where the keys are the current labels of the members of the transcript and the value for each key is a one word string that describes the role of the member of the transcript from the list ['customer', 'agent']
Only return the JSON structure.
transcript:
{redacted_chat_transcript}
""")
print(speaker_map.text)

 ```json
{
  "speaker 1": "customer",
  "speaker 2": "agent"
}
```


In [53]:
for key, val in json.loads(''.join(speaker_map.text.split('\n')[1:-1])).items():
    redacted_chat_transcript = redacted_chat_transcript.replace(key, val)

In [54]:
print(redacted_chat_transcript)


customer: Hello.
agent: Thank you for calling Google Cloud support. How may I assist you? Today, Mr. [LAST_NAME].
customer: Hi, I am trying to create a Google Cloud account and use the free credits but I am not sure where to start
agent: sure. I can definitely help you with that. May I know if you already have a Google account?
customer: Yes, I do. My account number is one two, three, four, five six, seven eight nine
agent: great. The first step would be to sign into the Google Cloud console. Do you know how to access it?
customer: No, I don't. Can you guide me?
agent: Sure, please go to [URL] and sign in with your Google account credentials. Once you are signed in you will be directed to the Google Cloud console dashboard.
customer: Okay, I have signed in what should I do next
agent: now, you'll need to create a project a project is a collection of resources such as compute engine instances and cloud storage buckets to create a project click on the projects Tab and then click on the 

In [55]:
text_model.predict(f"Summarize the following conversation: \n{redacted_chat_transcript}")

 A customer contacted Google Cloud support to set up an account and utilize the free credits offered. The agent guided the customer through the process, starting with signing in to the Google Cloud console using their existing Google account. They then explained how to create a project and enable the free trial by providing credit card information. The customer was informed that they would receive $300 worth of free credit valid for 12 months. The agent advised the customer to monitor their usage to avoid additional charges after the free trial period ends. The customer expressed gratitude for the assistance, and the conversation ended with the agent checking if there were any other concerns.

In [56]:
text_model.predict(f"Summarize the following conversation from the point of view of each speaker. Speaker 1 is new to Google Cloud and not certain how to get started. List 1 thing that could be done better to help each speaker.:\n{redacted_chat_transcript}", max_output_tokens = 600)

 **Customer:**

- I needed help creating a Google Cloud account and using the free credits.
- The agent guided me through the process of signing in, creating a project, and enabling the free trial.
- I received information about the amount of free credit I would get and how to monitor my usage.

**One thing that could be done better:**

- The agent could have provided a more detailed explanation of the different Google Cloud services and how they can be used.

**Agent:**

- I assisted the customer in creating a Google Cloud account and using the free credits.
- I provided step-by-step instructions on how to sign in, create a project, and enable the free trial.
- I answered the customer's questions about the amount of free credit they would receive and how to monitor their usage.

**One thing that could be done better:**

- I could have provided more information about the different Google Cloud services and how they can be used.

In [57]:
text_model.predict(f"Did the agent meet the customers needs in this transcript? What did they do well? What did not work? transcript:\n{redacted_chat_transcript}")

 **Did the agent meet the customer's needs?**

Yes, the agent met the customer's needs by providing clear and concise instructions on how to create a Google Cloud account, use the free credits, and enable the free trial. The agent also provided information on how much free credit the customer would receive and what to do when the credits are used up.

**What did they do well?**

The agent did a good job of:

- Identifying the customer's needs and providing step-by-step instructions on how to meet those needs.
- Providing clear and concise explanations of the different steps involved in